In [1]:
# 读取配置
from config_jingbo import *
# from config_tansuanli import *
# from config_juxiting import *
from lib.dataread import *
from lib.tools import *
from models.nerulforcastmodels import ex_Model,model_losss,brent_export_pdf,tansuanli_export_pdf,pp_export_pdf,model_losss_juxiting

import glob
import torch
torch.set_float32_matmul_precision("high")

sqlitedb = SQLiteHandler(db_name) 
sqlitedb.connect()

# def predict_main():
signature = BinanceAPI(APPID, SECRET)
etadata = EtaReader(signature=signature,
                        classifylisturl = classifylisturl,
                        classifyidlisturl=classifyidlisturl,
                        edbcodedataurl=edbcodedataurl,
                        edbcodelist=edbcodelist,
                        edbdatapushurl=edbdatapushurl,
                        edbdeleteurl=edbdeleteurl,
                        edbbusinessurl=edbbusinessurl
                        )
# 获取数据
if is_eta:
    # eta数据
    logger.info('从eta获取数据...')
    signature = BinanceAPI(APPID, SECRET)
    etadata = EtaReader(signature=signature,
                                classifylisturl = classifylisturl,
                                classifyidlisturl=classifyidlisturl,
                                edbcodedataurl=edbcodedataurl,
                                edbcodelist=edbcodelist,
                                edbdatapushurl=edbdatapushurl,
                                edbdeleteurl=edbdeleteurl,
                                edbbusinessurl=edbbusinessurl,
                                )

    # df_zhibiaoshuju,df_zhibiaoliebiao = etadata.get_eta_api_yuanyou_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理
    df_zhibiaoshuju,df_zhibiaoliebiao =  etadata.get_eta_api_pp_data(data_set=data_set,dataset=dataset)  # 原始数据，未处理

    
    # 数据处理
    df = datachuli(df_zhibiaoshuju,df_zhibiaoliebiao,y = y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time) 

else:
    logger.info('读取本地数据：'+os.path.join(dataset,data_set))
    df = getdata(filename=os.path.join(dataset,data_set),y=y,dataset=dataset,add_kdj=add_kdj,is_timefurture=is_timefurture,end_time=end_time)  # 原始数据，未处理

# 更改预测列名称
df.rename(columns={y:'y'},inplace=True)
    
if is_edbnamelist:
    df = df[edbnamelist]     
df.to_csv(os.path.join(dataset,'指标数据.csv'), index=False)
# 保存最新日期的y值到数据库
# 取第一行数据存储到数据库中
first_row = df[['ds','y']].tail(1)
# 将最新真实值保存到数据库
if not sqlitedb.check_table_exists('trueandpredict'):
    first_row.to_sql('trueandpredict',sqlitedb.connection,index=False)
else:
    for row in first_row.itertuples(index=False):
        row_dict = row._asdict()
        row_dict['ds'] = row_dict['ds'].strftime('%Y-%m-%d %H:%M:%S')
        check_query = sqlitedb.select_data('trueandpredict',where_condition = f"ds = '{row.ds}'")
        if len(check_query) > 0:
            set_clause = ", ".join([f"{key} = '{value}'" for key, value in row_dict.items()])
            sqlitedb.update_data('trueandpredict',set_clause,where_condition = f"ds = '{row.ds}'")
            continue
        sqlitedb.insert_data('trueandpredict',tuple(row_dict.values()),columns=row_dict.keys())

import datetime
# 判断当前日期是不是周一
is_weekday = datetime.datetime.now().weekday() == 4
if is_weekday:
    logger.info('今天是周一，更新预测模型')
    try:
        # 计算最近20天预测残差最低的模型名称

        model_results = sqlitedb.select_data('trueandpredict',order_by = "ds DESC",limit = "20")
        model_results = model_results.dropna()
        modelnames  = model_results.columns.to_list()[2:] 
        for col in model_results[modelnames].select_dtypes(include=['object']).columns:
            model_results[col] = model_results[col].astype(np.float32)
        # 计算每个预测值与真实值之间的偏差率
        for model in modelnames:
            model_results[f'{model}_abs_error_rate'] = abs(model_results['y'] - model_results[model]) / model_results['y']

        # 获取每行对应的最小偏差率值
        min_abs_error_rate_values = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].min(), axis=1)
        # 获取每行对应的最小偏差率值对应的列名
        min_abs_error_rate_column_name = model_results.apply(lambda row: row[[f'{model}_abs_error_rate' for model in modelnames]].idxmin(), axis=1)
        # 将列名索引转换为列名
        min_abs_error_rate_column_name = min_abs_error_rate_column_name.map(lambda x: x.split('_')[0])
        # 取出现次数最多的模型名称
        most_common_model = min_abs_error_rate_column_name.value_counts().idxmax()
        logger.info(f"最近20天预测残差最低的模型名称：{most_common_model}")
    except Exception as e:
        logger.error(f"最近20天预测残差最低的模型名称计算失败：{e}")
        # 取txt中的模型名称
        most_common_model = pd.read_csv(os.path.join(dataset,'best_modelnames.txt'),header=None).values.flatten().tolist()[0]

    # 保存结果到数据库
    
    if not sqlitedb.check_table_exists('most_model'):
        sqlitedb.create_table('most_model',columns="ds datetime, most_common_model TEXT")
    sqlitedb.insert_data('most_model',(datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'),most_common_model,),columns=('ds','most_common_model',))






if is_corr:
    df = corr_feature(df=df)

df1 = df.copy()  # 备份一下，后面特征筛选完之后加入ds y 列用

 


读取本地数据：dataset\原油指标数据.xlsx
getdata接收：dataset\原油指标数据.xlsx date 2024-10-27
删除两月不更新特征前数据量：(2492, 930)
删除两月不更新特征后数据量：(2492, 618)
删除预测列为空值的行后数据量：(1763, 618)
删除全为空值的列后数据量：(1763, 541)
d:\liurui\dev\code\PriceForecast\lib\dataread.py:135: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  values.dropna(inplace=True,axis=0)
d:\liurui\dev\code\PriceForecast\lib\dataread.py:135: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  values.dropna(inplace=True,axis=0)
d:\liurui\dev\code\PriceForecast\lib\dataread.py:135: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentat

<Figure size 1000x1000 with 0 Axes>

In [5]:
logger.info(f"开始训练模型...")
row,col = df.shape

now = datetime.datetime.now().strftime('%Y%m%d%H%M%S')
# ex_Model(df,
#         horizon=horizon,
#         input_size=input_size,
#         train_steps=train_steps,
#         val_check_steps=val_check_steps,
#         early_stop_patience_steps=early_stop_patience_steps,
#         is_debug=is_debug,
#         dataset=dataset,
#         is_train=is_train,
#         is_fivemodels=is_fivemodels,
#         val_size=val_size,
#         test_size=test_size,
#         settings=settings,
#         now=now,
#         etadata = etadata,
#         modelsindex = modelsindex,
#         data = data,
#         is_eta=is_eta,
#         )


logger.info('模型训练完成')

开始训练模型...
模型训练完成


In [2]:
# # 模型评估

logger.info('训练数据绘图ing')
model_results3 = model_losss_juxiting(sqlitedb)

logger.info('训练数据绘图end')
# 模型报告

# logger.info('制作报告ing')
# title = f'{settings}--{now}-预测报告' # 报告标题
# brent_export_pdf(dataset=dataset,num_models = 5 if is_fivemodels else 22,time=end_time,
#       reportname=reportname,sqlitedb=sqlitedb),
# # pp_export_pdf(dataset=dataset,num_models = 5 if is_fivemodels else 22,time=end_time,
#       # reportname=reportname),
# logger.info('制作报告end')
# logger.info('模型训练完成')

训练数据绘图ing
--- Logging error ---
Traceback (most recent call last):
  File "d:\ProgramData\anaconda3\Lib\logging\handlers.py", line 73, in emit
    if self.shouldRollover(record):
       ^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "d:\ProgramData\anaconda3\Lib\logging\handlers.py", line 196, in shouldRollover
    msg = "%s\n" % self.format(record)
                   ^^^^^^^^^^^^^^^^^^^
  File "d:\ProgramData\anaconda3\Lib\logging\__init__.py", line 953, in format
    return fmt.format(record)
           ^^^^^^^^^^^^^^^^^^
  File "d:\ProgramData\anaconda3\Lib\logging\__init__.py", line 687, in format
    record.message = record.getMessage()
                     ^^^^^^^^^^^^^^^^^^^
  File "d:\ProgramData\anaconda3\Lib\logging\__init__.py", line 377, in getMessage
    msg = msg % self.args
          ~~~~^~~~~~~~~~~
TypeError: not all arguments converted during string formatting
Call stack:
  File "<frozen runpy>", line 198, in _run_module_as_main
  File "<frozen runpy>", line 88, in _run_code
  Fil

            ds      NHITS   Informer       LSTM  iTransformer    TSMixer  \
0   2024-01-19  78.276070  76.027702  79.778801     78.265656  77.692642   
5   2024-01-22  78.223007  76.392143  79.033913     77.764168  77.695419   
10  2024-01-23  79.732689  77.411430  80.672409     77.617729  78.866539   
15  2024-01-24  78.661491  77.809235  80.039368     78.195992  78.749481   
20  2024-01-25  79.844170  77.678902  80.665665     76.032829  78.895386   
..         ...        ...        ...        ...           ...        ...   
975 2024-10-21  72.710213  73.392860  73.882164     75.144104  73.823708   
976 2024-10-22  73.478493  73.580597  73.937225     74.912628  74.266403   
977 2024-10-23  72.304123  73.170967  74.000931     74.571083  74.419685   
978 2024-10-24  74.337288  73.285072  73.991661     74.442238  74.568016   
979 2024-10-25  74.662025  73.347038  74.131668     74.182922  74.496666   

      TSMixerx   PatchTST        RNN        GRU  ...        TFT    StemGNN  \
0    77.9

d:\liurui\dev\code\PriceForecast\models\nerulforcastmodels.py:738: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  check_query = sqlitedb.select_data('trueandpredict',where_condition = f"ds = '{row.ds}'")
更新数据sqlUPDATE trueandpredict SET ds = '2024-10-28 00:00:00', NHITS = '72.375534', Informer = '77.86241', LSTM = '76.698364', iTransformer = '75.98318', TSMixer = '75.15075', TSMixerx = '74.38121', PatchTST = '75.594734', RNN = '53.52923', GRU = '77.05893', TCN = '74.90376', BiTCN = '75.4683', DilatedRNN = '77.86542', MLP = '74.50678', DLinear = '75.67038', NLinear = '75.36442', TFT = '73.99709', StemGNN = '74.57198', MLPMultivariate = '74.20644', TiDE = '75.10396', DeepNPTS = '74.762405' WHERE ds = '2024-10-28 00:00:00'


Column 'ds' already exists in table 'trueandpredict'.
Column 'NHITS' already exists in table 'trueandpredict'.
Column 'Informer' already exists in table 'trueandpredict'.
Column 'LSTM' already exists in table 'trueandpredict'.
Column 'iTransformer' already exists in table 'trueandpredict'.
Column 'TSMixer' already exists in table 'trueandpredict'.
Column 'TSMixerx' already exists in table 'trueandpredict'.
Column 'PatchTST' already exists in table 'trueandpredict'.
Column 'RNN' already exists in table 'trueandpredict'.
Column 'GRU' already exists in table 'trueandpredict'.
Column 'TCN' already exists in table 'trueandpredict'.
Column 'BiTCN' already exists in table 'trueandpredict'.
Column 'DilatedRNN' already exists in table 'trueandpredict'.
Column 'MLP' already exists in table 'trueandpredict'.
Column 'DLinear' already exists in table 'trueandpredict'.
Column 'NLinear' already exists in table 'trueandpredict'.
Column 'TFT' already exists in table 'trueandpredict'.
Column 'StemGNN' a

posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
posx and posy should be finite values
训练数据绘图end
制作报告ing
开始绘制Kpler数据--原油出口类指标的相关性直方图
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):


...

d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

正在绘制第5个特征荷兰陆上原油库存与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

运输下正相关的特征值有： ['莱茵河水位']
正在绘制第1个特征莱茵河水位与价格散点图...


d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating instead.
  with pd.option_context('mode.use_inf_as_na', True):
d:\ProgramData\anaconda3\Lib\site-packages\seaborn\_oldcore.py:1119: FutureWarning: use_inf_as_na option is deprecated and will be removed in a future version. Convert inf values to NaN before operating

In [ ]:
# 发送邮件
m = SendMail(
    username=username,
    passwd=passwd,
    recv=recv,
    title=title,
    content=content,
    file=max(glob.glob(os.path.join(dataset,'*.pdf')), key=os.path.getctime),
    ssl=ssl,
)
m.send_mail()   